In [ ]:
openai_key = "sk-wiPainMePj57Yo2bfpYbaGDkCD-mD_uyzU0E9t66LNT3BlbkFJHhxKXtycZrk1N6a9ln6M__k5c6MG6Lh5V5emcpkhsA"

In [ ]:
!pip install openai pdf2image pillow
!apt-get install -y poppler-utils

import os
import re
import json
import time
import base64
import pandas as pd
import openai
from openai import (
    OpenAI,
    APITimeoutError,
    APIConnectionError,
    RateLimitError,
    InternalServerError,
)
from pdf2image import convert_from_path


pdf_path = "/content/NEET_2020_Kannada_F1.pdf"

language = "Kannada"
page_start = 0
page_end = 29  # Adjust as needed
source = "https://images.collegedunia.com/public/college_data/images/entrance/sample_paper/1640593808NEET%202020%20Kannada%20F1%20QP.pdf"

# Pre-prompt for GPT
pre_prompt = """Please extract the multiple-choice questions in the attached image in the {} language in which they appear. There can be one or multiple questions per page. The question number should be inside the <question_num></question_num> tags, the question should be inside the tags  <question> </question> and the choices inside the tags <choices> </choices>. Also, determine the category of question from the following - physics, chemistry, botany, zoology. Like if it belongs to chemistry output <category>chemistry</category>. If the question requires some image or a figure to arrive at an answer respond with <image>yes</image> else respond with <image>no</image>. If a particular question requires referring to a passage, respond with <context>yes</context> else respond with <context>no</context>. Additionally, the correct answer might be present in the image either explicitly provided or by a mark next to the correct answer of the multiple choices. Provide the number or letter of the correct answer between the tags <answer> </answer>. If no answer is present, leave empty.
The output format should be the following, depending on the number of choices present:
<question> </question>
<choices>
</choices>
<answer> </answer>
<image></image>
<context></context>
<category></category>
"""

# Category mapping function
def map_category_to_subject(category):
    category_map = {
        "physics": {"en": "Physics", "kn": "ಭೌತಶಾಸ್ತ್ರ"},
        "chemistry": {"en": "Chemistry", "kn": "ರಸಾಯನಶಾಸ್ತ್ರ"},
        "botany": {"en": "Botany", "kn": "ಸಸ್ಯಶಾಸ್ತ್ರ"},
        "zoology": {"en": "Zoology", "kn": "ಪ್ರಾಣಿಶಾಸ್ತ್ರ"},
    }
    return category_map.get(category.lower(), {"en": "Unknown", "kn": "ಅಜ್ಞಾತ"})  # Default to 'Unknown' if no match is found


# Functions for parsing and GPT interaction
def parse_gpt_output(response, pdf_path):
    # Regex patterns for extracting data
    question_pattern = re.compile(r"<question>(.*?)</question>", re.DOTALL)
    choices_pattern = re.compile(r"<choices>(.*?)</choices>", re.DOTALL)
    answer_pattern = re.compile(r"<answer>(.*?)</answer>", re.DOTALL)
    requires_image_pattern = re.compile(r"<image>(.*?)</image>", re.DOTALL)
    category_pattern = re.compile(r"<category>(.*?)</category>", re.DOTALL)
    context_pattern = re.compile(r"<context>(.*?)</context>", re.DOTALL)
    question_num_pattern = re.compile(r"<question_num>(.*?)</question_num>", re.DOTALL)

    # Extract matches
    question_matches = question_pattern.findall(response)
    choices_matches = choices_pattern.findall(response)
    requires_image = requires_image_pattern.findall(response)
    contexts = context_pattern.findall(response)
    categories = category_pattern.findall(response)
    q_nums = question_num_pattern.findall(response)

    # Map categories to one of the four subjects
    mapped_categories = [map_category_to_subject(cat) for cat in categories]

    # Parsing choices based on PDF type
    final_matches = []
    for choice_match in choices_matches:
        if choice_match:
            # Capture all options within the choices string
            options = re.findall(r"\(\d\) ([^\n]+)", choice_match)
            if not options:  # For formats like (A), (B), (C), (D)
                options = re.findall(r"\(([A-Z])\) ([^\n]+)", choice_match)
                options = [opt[1] for opt in options]  # Extract the text portion
            final_matches.append(options)
        else:
            final_matches.append([])

    return (
        question_matches,
        final_matches,
        requires_image,
        mapped_categories,
        contexts,
        q_nums,
    )

def chat_completion(
    client,
    messages,
    model,
    return_text=True,
    return_usage=True,
    model_args=None,
):
    """
    Calls OpenAI API with the image and the prompt
    """
    if model_args is None:
        model_args = {}

    while True:
        try:
            response = client.chat.completions.create(
                model=model, messages=messages, **model_args
            )
            text = response.choices[0].message.content.strip()
            usage = response.usage

            if return_text and return_usage:
                return text, dict(usage)

            if return_text:
                return text

            if return_usage:
                return usage

            return response
        except (
            APITimeoutError,
            APIConnectionError,
            RateLimitError,
            InternalServerError,
        ) as e:
            print(f"OpenAI error: {str(e)}. Waiting for 1 minute.")
            time.sleep(60)
            continue

def encode_image(image_path):
    """
    Function to encode the image
    """
    with open(image_path, "rb") as image_file:
        return base64.b64encode(image_file.read()).decode("utf-8")

# Main function
def main(pdf_path, openai_key, language, page_start=0, page_end=9999, source=""):
    """
    It performs the main text extraction pipeline of the script.
    """
    # Create OpenAI client
    client = OpenAI(api_key=openai_key)

    pdf_name = "1640593808NEET%202020%20Kannada%20F1%20QP.pdf"

    # Define paths for 'imgs' and 'results' folders
    parent_directory = os.path.dirname(os.path.dirname(pdf_path))
    imgs_folder = os.path.join(parent_directory, "imgs", pdf_name)
    result_path = "/content/results"  # Explicit path

    # Create directories if they don't exist
    os.makedirs(imgs_folder, exist_ok=True)
    os.makedirs(result_path, exist_ok=True)

    # Debugging output to check directory paths
    print(f"Images folder: {imgs_folder}")
    print(f"Results folder: {result_path}")

    images = convert_from_path(pdf_path, first_page=1)
    images = images[page_start:page_end]
    page_num = page_start + 1

    # Process each image
    results = list()
    q_idx = 0
    for _, image in enumerate(images):
        print(f"Page: {page_num} / {len(images)}")
        image_path = os.path.join(imgs_folder, f"page_{page_num+1}.png")
        image.save(image_path, "PNG")
        base64_image = encode_image(image_path)

        # Pass image to GPT-4 for MCQ extraction
        try:
            message = [
                {"type": "text", "text": pre_prompt.format(language)},
                {
                    "type": "image_url",
                    "image_url": {"url": f"data:image/jpeg;base64,{base64_image}"},
                },
            ]
            response, _ = chat_completion(
                client,
                [{"role": "user", "content": message}],
                model="gpt-4o",
                return_text=True,
                return_usage=True,
                model_args={
                    "temperature": 0.0,
                    "max_tokens": 4096,
                    "top_p": 1,
                    "frequency_penalty": 0,
                    "presence_penalty": 0,
                },
            )
            # Log the response for analysis
            print(f"Response for page {page_num}:\n{response}")

            # Process GPT-4 output
            (
                questions,
                choices,
                requires_image,
                mapped_categories,
                contexts,
                q_nums,
            ) = parse_gpt_output(response, pdf_path)

            # Check if all extracted elements have the same length
            if not all(
                len(lst) == len(questions)
                for lst in [
                    choices,
                    requires_image,
                    mapped_categories,
                    contexts,
                    q_nums,
                ]
            ):
                print(f"Inconsistency detected on page {page_num}:")
                print(f"Questions: {len(questions)}, Choices: {len(choices)}, "
                      f"Requires Image: {len(requires_image)}, Mapped Categories: {len(mapped_categories)}, "
                      f"Contexts: {len(contexts)}, Question Numbers: {len(q_nums)}")

                # Handle inconsistencies by only considering consistent entries
                min_length = min(len(questions), len(choices), len(requires_image), len(mapped_categories), len(contexts), len(q_nums))

                # Truncate lists to the minimum consistent length
                questions = questions[:min_length]
                choices = choices[:min_length]
                requires_image = requires_image[:min_length]
                mapped_categories = mapped_categories[:min_length]
                contexts = contexts[:min_length]
                q_nums = q_nums[:min_length]

                print(f"After truncation: Questions: {len(questions)}, Choices: {len(choices)}, "
                      f"Requires Image: {len(requires_image)}, Mapped Categories: {len(mapped_categories)}, "
                      f"Contexts: {len(contexts)}, Question Numbers: {len(q_nums)}")
            else:
                print(f"Page {page_num} is consistent.")

            page_results = []
            for question, options, has_image, category, cntx, q_num in zip(
                questions,
                choices,
                requires_image,
                mapped_categories,
                contexts,
                q_nums,
            ):
                new_row = {
                    "language": "kn",  # Set language to Kannada's language code 'kn'
                    "country": "India",  # Set country to India
                    "file_name": pdf_name,
                    "source": source,
                    "license": "open",  # Assuming open, adjust if needed
                    "level": "University",
                    "category_en": category["en"],
                    "category_original_lang": category["kn"],  # Kannada translation
                    "original_question_idx": q_num,
                    "page_num": page_num,
                    "question": question,
                    "options": options,
                    "answer": "",
                    "requires_image": has_image,
                    "context": cntx,
                }
                page_results.append(new_row)
                q_idx += 1

            # Save the results to a JSON file without including the raw response
            output_file = os.path.join(result_path, pdf_name + f"_page_{page_num}.json")
            print(f"Saving data to: {output_file}")
            with open(output_file, "w", encoding="utf-8") as json_file:
                json.dump(page_results, json_file, indent=4, ensure_ascii=False)
            print(f"Data saved: {output_file}")

            page_num += 1

        except openai.BadRequestError as e:
            print(f"Error on page {page_num}: {str(e)}")
            pass

        except Exception as e:
            print(f"Unexpected error: {str(e)}")

# Run the main function in Colab
main(
    pdf_path=pdf_path,
    openai_key=openai_key,
    language=language,
    page_start=page_start,
    page_end=page_end,
    source=source,
)

# List the contents of the results directory for verification
!ls /content/results


Reading package lists... Done
Building dependency tree... Done
Reading state information... Done
poppler-utils is already the newest version (22.02.0-2ubuntu0.5).
0 upgraded, 0 newly installed, 0 to remove and 49 not upgraded.
Images folder: /imgs/1640593808NEET%202020%20Kannada%20F1%20QP.pdf
Results folder: /content/results
Page: 1 / 22
Response for page 1:
<question_num>1</question_num>
<question>ಚೆಲವಣ ಪ್ರಕ್ರಿಯೆಯಲ್ಲಿ ಎಲೆಕ್ಟ್ರಾನರ್ ವಹನಕವಾಯು ಉಂಗಮಗಳು ಹಾಜರಿರುವುದು ಯಾವದ ಹಂತದಲ್ಲಿ :</question>
<choices>
(1) PS-I ನಿಂದ NADP+ ಗೆ
(2) PS-I ನಿಂದ ATP synthase ಗೆ
(3) PS-II ನಿಂದ Cyto b6f ಸಂಕೀರ್ಣಕ್ಕೆ
(4) Cyto b6f ಸಂಕೀರ್ಣದಿಂದ PS-I ಗೆ
</choices>
<answer>3</answer>
<image>no</image>
<context>no</context>
<category>botany</category>

<question_num>2</question_num>
<question>ಕೋಲಿಬಾಸಿಲಸ್ ಡಿ.ಎನ್.ಎ.ಯ ಪ್ರತಿಕ್ರಿಯ ಸಂಯೋಜಕವು, ವಾಹಕ (vector) ದಲ್ಲಿ ನಿಯೋಜಿಸಲ್ಪಡುವ ಅಂಶಗಳಲ್ಲಿ ಒಂದನ್ನು ಪತ್ತೆಹಚ್ಚಿ :</question>
<choices>
(1) ಪ್ರಾರಂಭ ಅಂಶಮೂಲಕ
(2) ಗುರತಿಸುವ ಜಾಗ
(3) ಆಮ್ಲಜನಕದ ಗುರತಿಗ
(4) Ori ಜಾಗ
</choices>
<answer>4</answer>
<image>

In [ ]:
import os
import json
import pandas as pd

# Directory where your JSON files are stored
json_dir = '/content/results'

# List all JSON files in the directory
json_files = [pos_json for pos_json in os.listdir(json_dir) if pos_json.endswith('.json')]

# Initialize an empty list to hold each DataFrame
dataframes = []

# Loop over each JSON file and append to the list of DataFrames
for file in json_files:
    file_path = os.path.join(json_dir, file)
    with open(file_path, 'r', encoding='utf-8') as f:
        data = json.load(f)
        # Convert each JSON object to a DataFrame and append to the list
        df = pd.DataFrame(data)
        dataframes.append(df)

# Concatenate all DataFrames into one
final_df = pd.concat(dataframes, ignore_index=True)

# Save the merged DataFrame to a new JSON or CSV file if needed
merged_json_path = '/content/merged_results.json'
final_df.to_json(merged_json_path, orient='records', indent=4, force_ascii=False)

# Optionally, save as CSV
merged_csv_path = '/content/merged_results.csv'
final_df.to_csv(merged_csv_path, index=False, encoding='utf-8')


In [ ]:
import pandas as pd

# Load the CSV file
csv_file_path = '/content/merged_results.csv'
df = pd.read_csv(csv_file_path)

# Convert to JSON
#json_file_path = '/content/kannada_neet_2020.json'
#df.to_json(json_file_path, orient='records', indent=4, force_ascii=False)

#print(f"Converted CSV to JSON: {json_file_path}")


In [ ]:
df

language country                                      file_name  \
0         kn   India  1640593808NEET%202020%20Kannada%20F1%20QP.pdf   
1         kn   India  1640593808NEET%202020%20Kannada%20F1%20QP.pdf   
2         kn   India  1640593808NEET%202020%20Kannada%20F1%20QP.pdf   
3         kn   India  1640593808NEET%202020%20Kannada%20F1%20QP.pdf   
4         kn   India  1640593808NEET%202020%20Kannada%20F1%20QP.pdf   
..       ...     ...                                            ...   
146       kn   India  1640593808NEET%202020%20Kannada%20F1%20QP.pdf   
147       kn   India  1640593808NEET%202020%20Kannada%20F1%20QP.pdf   
148       kn   India  1640593808NEET%202020%20Kannada%20F1%20QP.pdf   
149       kn   India  1640593808NEET%202020%20Kannada%20F1%20QP.pdf   
150       kn   India  1640593808NEET%202020%20Kannada%20F1%20QP.pdf   

                                                source license       level  \
0    https://images.collegedunia.com/public/college...    open  University   
1    https://images.collegedunia.com/public/college...    open  University   
2    https://images.collegedunia.com/public/college...    open  University   
3    https://images.collegedunia.com/public/college...    open  University   
4    https://images.collegedunia.com/public/college...    open  University   
..                                                 ...     ...         ...   
146  https://images.collegedunia.com/public/college...    open  University   
147  https://images.collegedunia.com/public/college...    open  University   
148  https://images.collegedunia.com/public/college...    open  University   
149  https://images.collegedunia.com/public/college...    open  University   
150  https://images.collegedunia.com/public/college...    open  University   

    category_en category_original_lang  original_question_idx  page_num  \
0        Botany            ಸಸ್ಯಶಾಸ್ತ್ರ                     27         4   
1       Physics             ಭೌತಶಾಸ್ತ್ರ                     99        12   
2       Physics             ಭೌತಶಾಸ್ತ್ರ                    100        12   
3       Physics             ಭೌತಶಾಸ್ತ್ರ                    101        12   
4       Physics             ಭೌತಶಾಸ್ತ್ರ                    102        12   
..          ...                    ...                    ...       ...   
146      Botany            ಸಸ್ಯಶಾಸ್ತ್ರ                     83        10   
147      Botany            ಸಸ್ಯಶಾಸ್ತ್ರ                     84        10   
148   Chemistry           ರಸಾಯನಶಾಸ್ತ್ರ                     85        10   
149      Botany            ಸಸ್ಯಶಾಸ್ತ್ರ                     86        10   
150   Chemistry           ರಸಾಯನಶಾಸ್ತ್ರ                     87        10   

                                              question  \
0    ಕೆಳಗಿನ ಕಾಲಮಗಳನ್ನು, ಹೊಂದಿದ ಮತ್ತು ಸಂಯೋಜಿಸಿದ ಜೋಡಿ...   
1    50 ವಿಭಾಗಗಳಿರುವ ಪ್ರತ್ಯೇಕದ ಸ್ಕೇಲ್ ಮತ್ತು 0.01 mm ...   
2    ಸದರ ಸಂಗತ ಚಲನೆಯಲ್ಲಿರುವ ಕಣದ ಸ್ಕಾಂತದ ಮತ್ತು ವೇಗದ್ವ...   
3    2.5 A ವಿದ್ಯುತ್ ಪ್ರಬಲವಿರುವ 50 cm ಉದ್ದದ ತಂತುವಿನಲ...   
4    ಒಂದು ಗೋಪುರದ ಮೇಲಿಂದ 20 m/s ವೇಗದಲ್ಲಿ ಲಂಬವಾಗಿ ಕೆಳ...   
..                                                 ...   
146  ವಿಶ್ವಸಂಸ್ಥೆಯ ಪ್ರಥಮ ಜೈವಿಕನ್ಯಾಸ ತತ್ವದ ಉದಾಹರಣೆ ಯಾ...   
147  ಕೆಳಗಿನವನ್ನೆಲ್ಲಾ ಹೊಂದಿಸಿ ಮತ್ತು ಸರಿಯಾದ ಉತ್ತರವನ್ನ...   
148  ಕೆಳಗಿನ ಕಾನ್ಸೆಪ್ಟುಗಳನ್ನು ಹೊಂದಿಸಿ ಮತ್ತು ಸರಿಯಾದ ಉ...   
149  ಬೀಜದ ಸಮುದಾಯದಿಂದ ಪ್ರಥಮವಾಗಿ ಹೊರಹೊಮ್ಮುವ ಭಾಗ ಯಾವ ಕ...   
150  ಕೆಳಗಿನ ಕಾನ್ಸೆಪ್ಟುಗಳನ್ನು ಹೊಂದಿಸಿ ಮತ್ತು ಸರಿಯಾದ ಉ...   

                                               options  answer requires_image  \
0    ['(a) (b) (c) (d)', '(i) (ii) (iii) (iv)', '(i...     NaN             no   
1           ['0.5 mm', '1.0 mm', '0.01 mm', '0.25 mm']     NaN             no   
2        ['π/2 rad', '0 (ಶೂನ್ಯ)', 'π rad', '3π/2 rad']     NaN             no   
3    ['6.28 x 10⁻⁵ T', '3.14 x 10⁻⁵ T', '6.28 x 10⁻...     NaN             no   
4                 ['320 m', '300 m', '360 m', '340 m']     NaN             no   
..                                                 ...     ...            ...   
146  ['ಜಾರ್ವಿಸ್ ಡಾರ್ವಿನ್', 'ಲಾಮಾರ್ಕ್', 'ಡಾರ್ವಿನ್ 

In [ ]:
df.columns

Index(['language', 'country', 'file_name', 'source', 'license', 'level',
       'category_en', 'category_original_lang', 'original_question_idx',
       'page_num', 'question', 'options', 'answer', 'requires_image',
       'context'],
      dtype='object')

In [ ]:
import pandas as pd

# Assuming you have already loaded your DataFrame
# Rename 'original_question_idx' to 'original_question_num'
df.rename(columns={'original_question_idx': 'original_question_num'}, inplace=True)

# Now, let's test that the column name has been changed
print("Updated DataFrame columns:")
print(df.columns)

Updated DataFrame columns:
Index(['language', 'country', 'file_name', 'source', 'license', 'level',
       'category_en', 'category_original_lang', 'original_question_num',
       'page_num', 'question', 'options', 'answer', 'requires_image',
       'context'],
      dtype='object')


In [ ]:
import pandas as pd

# Sample JSON data extracted from the PDF as an answer key
answer_key_json = {
    "1": "3", "2": "4", "3": "3", "4": "1", "5": "2", "6": "1", "7": "4", "8": "2",
    "9": "3", "10": "1", "11": "1", "12": "4", "13": "1", "14": "1", "15": "3", "16": "3",
    "17": "3", "18": "4", "19": "2", "20": "4", "21": "3", "22": "3", "23": "4", "24": "2",
    "25": "2", "26": "2", "27": "4", "28": "1", "29": "2", "30": "1", "31": "2", "32": "4",
    "33": "1", "34": "1", "35": "1", "36": "4", "37": "4", "38": "4", "39": "3", "40": "3",
    "41": "3", "42": "4", "43": "4", "44": "4", "45": "1", "46": "4", "47": "4", "48": "1",
    "49": "2", "50": "2", "51": "3", "52": "1", "53": "1", "54": "4", "55": "3", "56": "1",
    "57": "4", "58": "1", "59": "2", "60": "1", "61": "4", "62": "2", "63": "3", "64": "4",
    "65": "3", "66": "3", "67": "3", "68": "3", "69": "4", "70": "4", "71": "2", "72": "2",
    "73": "2", "74": "1", "75": "2", "76": "1", "77": "3", "78": "1", "79": "3", "80": "2",
    "81": "3", "82": "1", "83": "3", "84": "3", "85": "4", "86": "3", "87": "1", "88": "4",
    "89": "1", "90": "4", "91": "4", "92": "1", "93": "2", "94": "2", "95": "2", "96": "1",
    "97": "2", "98": "2", "99": "1", "100": "3", "101": "3", "102": "2", "103": "2", "104": "1",
    "105": "1", "106": "4", "107": "2", "108": "1", "109": "3", "110": "3", "111": "4", "112": "4",
    "113": "2", "114": "4", "115": "1", "116": "4", "117": "3", "118": "1", "119": "1", "120": "4",
    "121": "3", "122": "1", "123": "4", "124": "3", "125": "1", "126": "4", "127": "1", "128": "3",
    "129": "4", "130": "4", "131": "1", "132": "4", "133": "4", "134": "4", "135": "1", "136": "2",
    "137": "1", "138": "2", "139": "3", "140": "4", "141": "1", "142": "2", "143": "2", "144": "1",
    "145": "3", "146": "1", "147": "2", "148": "2", "149": "3", "150": "4", "151": "1", "152": "3",
    "153": "1", "154": "3", "155": "3", "156": "2", "157": "3", "158": "4", "159": "1", "160": "3",
    "161": "3", "162": "1", "163": "1", "164": "1", "165": "2", "166": "4", "167": "2", "168": "2",
    "169": "4", "170": "3", "171": "3", "172": "3", "173": "4", "174": "1", "175": "1", "176": "2",
    "177": "3", "178": "3", "179": "1", "180": "2"
}

# Convert JSON to DataFrame
answer_df = pd.DataFrame(list(answer_key_json.items()), columns=['original_question_num', 'answer'])

# Convert 'original_question_num' to the same type as in your questions DataFrame
answer_df['original_question_num'] = answer_df['original_question_num'].astype(int)

# Assuming your questions DataFrame is named df
# Merge the answer_df with your main DataFrame (df)
merged_df = df.merge(answer_df, on='original_question_num', how='left')

# Drop the placeholder answer column
merged_df.drop(columns=['answer_x'], inplace=True)

# Rename the new answer column to 'answer'
merged_df.rename(columns={'answer_y': 'answer'}, inplace=True)

# Save or display the merged DataFrame
merged_csv_path = '/content/merged_results_with_answers.csv'
merged_df.to_csv(merged_csv_path, index=False, encoding='utf-8')

# Display the updated DataFrame
merged_df.head()


language country                                      file_name  \
0       kn   India  1640593808NEET%202020%20Kannada%20F1%20QP.pdf   
1       kn   India  1640593808NEET%202020%20Kannada%20F1%20QP.pdf   
2       kn   India  1640593808NEET%202020%20Kannada%20F1%20QP.pdf   
3       kn   India  1640593808NEET%202020%20Kannada%20F1%20QP.pdf   
4       kn   India  1640593808NEET%202020%20Kannada%20F1%20QP.pdf   

                                              source license       level  \
0  https://images.collegedunia.com/public/college...    open  University   
1  https://images.collegedunia.com/public/college...    open  University   
2  https://images.collegedunia.com/public/college...    open  University   
3  https://images.collegedunia.com/public/college...    open  University   
4  https://images.collegedunia.com/public/college...    open  University   

  category_en category_original_lang  original_question_num  page_num  \
0      Botany            ಸಸ್ಯಶಾಸ್ತ್ರ                     27         4   
1     Physics             ಭೌತಶಾಸ್ತ್ರ                     99        12   
2     Physics             ಭೌತಶಾಸ್ತ್ರ                    100        12   
3     Physics             ಭೌತಶಾಸ್ತ್ರ                    101        12   
4     Physics             ಭೌತಶಾಸ್ತ್ರ                    102        12   

                                            question  \
0  ಕೆಳಗಿನ ಕಾಲಮಗಳನ್ನು, ಹೊಂದಿದ ಮತ್ತು ಸಂಯೋಜಿಸಿದ ಜೋಡಿ...   
1  50 ವಿಭಾಗಗಳಿರುವ ಪ್ರತ್ಯೇಕದ ಸ್ಕೇಲ್ ಮತ್ತು 0.01 mm ...   
2  ಸದರ ಸಂಗತ ಚಲನೆಯಲ್ಲಿರುವ ಕಣದ ಸ್ಕಾಂತದ ಮತ್ತು ವೇಗದ್ವ...   
3  2.5 A ವಿದ್ಯುತ್ ಪ್ರಬಲವಿರುವ 50 cm ಉದ್ದದ ತಂತುವಿನಲ...   
4  ಒಂದು ಗೋಪುರದ ಮೇಲಿಂದ 20 m/s ವೇಗದಲ್ಲಿ ಲಂಬವಾಗಿ ಕೆಳ...   

                                             options requires_image context  \
0  ['(a) (b) (c) (d)', '(i) (ii) (iii) (iv)', '(i...             no      no   
1         ['0.5 mm', '1.0 mm', '0.01 mm', '0.25 mm']             no      no   
2      ['π/2 rad', '0 (ಶೂನ್ಯ)', 'π rad', '3π/2 rad']             no      no   
3  ['6.28 x 10⁻⁵ T', '3.14 x 10⁻⁵ T', '6.28 x 10⁻...             no      no   
4               ['320 m', '300 m', '360 m', '340 m']             no      no   

  answer  
0      4  
1      1  
2      3  
3      3  
4      2

In [ ]:
# Convert the merged DataFrame to JSON
merged_json_path = '/content/merged_results_with_answers.json'
merged_df.to_json(merged_json_path, orient='records', indent=4, force_ascii=False)

# Display the path to the JSON file
print(f"Converted CSV to JSON: {merged_json_path}")


Converted CSV to JSON: /content/merged_results_with_answers.json


In [ ]:
!pip install rich

import json
import os
from datetime import datetime
import re
from rich.console import Console
from rich.panel import Panel
from rich.tree import Tree
from rich.text import Text
from rich.syntax import Syntax
from typing import Union  # Import Union from typing

class JSONEvaluator:
    def __init__(self, json_file=None, purge_error_entries=False):
        self.json_file = json_file
        self.json_data = []
        self.purge_error_entries = purge_error_entries
        self.output_file = None
        self.schema = {
            "language": str, "country": str, "file_name": str, "source": str,
            "license": str, "level": str, "category_en": str,
            "category_original_lang": str, "original_question_num": Union[int, str],
            "question": str, "options": list, "answer": str,
        }
        self.console = Console()

    def load_json_file(self):
        self.console.print(f"[cyan]Loading JSON file:[/cyan] {self.json_file}")
        try:
            with open(self.json_file, 'r', encoding='utf-8') as file:
                data = json.load(file)
                if not isinstance(data, list):
                    raise ValueError(f"File {self.json_file}: JSON should be a list of entries.")
                self.json_data = data
            return True
        except (json.JSONDecodeError, Exception) as e:
            self.console.print(f"[red]Error loading file {self.json_file}: {e}[/red]")
            return False

    def is_valid_iso_code(self, code):
        return bool(re.match(r'^[a-z]{2,3}$', code, re.IGNORECASE))

    def validate_entry(self, idx, entry):
        errors = []
        for key, expected_type in self.schema.items():
            value = entry.get(key)
            if value is None or (isinstance(value, str) and not value.strip()):
                errors.append({"entry": idx, "message": f"Missing or empty key '{key}'."})
            elif not isinstance(value, expected_type):
                errors.append({"entry": idx, "message": f"Invalid type for '{key}': expected {expected_type.__name__}, got {type(value).__name__}."})

        lang = entry.get('language', '').lower()
        if lang and not self.is_valid_iso_code(lang):
            errors.append({"entry": idx, "message": f"Invalid language code: '{lang}'. Must be a valid ISO 639-1 (2-letter)"})

        options = entry.get("options", [])
        if not isinstance(options, list) or any(not isinstance(opt, str) or not opt.strip() for opt in options):
            errors.append({"entry": idx, "message": "Invalid 'options': must be a list of non-empty strings."})
        elif len(set(options)) == 1:
            errors.append({"entry": idx, "message": "All options are identical."})

        answer = entry.get("answer", "")
        if not isinstance(answer, str):
            errors.append({"entry": idx, "message": "Invalid 'answer': must be a string."})
        else:
            try:
                answer_ints = [int(a.strip()) for a in answer.split(',')]
                valid_range = set(range(1, len(options) + 1))
                if not set(answer_ints).issubset(valid_range):
                    errors.append({"entry": idx, "message": f"Invalid 'answer': Answer cannot be more than number of options: {len(options)}."})
            except ValueError:
                errors.append({"entry": idx, "message": "Invalid 'answer': must be comma-separated integers."})

        return errors

    def validate_all(self):
        seen_entries = {}
        all_errors = []
        for idx, entry in enumerate(self.json_data):
            entry_hash = (entry['question'].strip(), tuple(opt.strip() for opt in entry['options']))

            if entry_hash in seen_entries:
                all_errors.append({"entry": idx, "message": f"Duplicate of entry {seen_entries[entry_hash]}."})
            else:
                seen_entries[entry_hash] = idx

            all_errors.extend(self.validate_entry(idx, entry))

        if all_errors:
            self.display_errors_pretty(all_errors)
            if self.purge_error_entries:
                self.remove_problematic_entries(all_errors)
            else:
                self.console.print("[bold bright_red]Validation issues found. Please fix them manually.[/bold bright_red]")
        return len(all_errors) == 0

    def display_errors_pretty(self, errors):
        console = Console()

        for error in errors:
            entry = self.json_data[error["entry"]]

            tree = Tree(f"[bold red]Error in Entry {error['entry']}[/bold red]")
            tree.add(Text(error['message'], style="bold yellow"))

            question_node = tree.add("Question")
            question_node.add(Syntax(entry.get('question', '[N/A]'), "text", theme="monokai", word_wrap=True))

            options_node = tree.add("Options")
            options = entry.get('options', [])
            for i, option in enumerate(options, 1):
                options_node.add(f"{i}. {option}")

            answer_node = tree.add("Answer")
            answer_node.add(str(entry.get('answer', '[N/A]')))

            console.print(Panel(tree, expand=False, border_style="red"))
            console.print()

    def check_for_duplicates(self):
        seen = {}
        duplicates = []
        for idx, entry in enumerate(self.json_data):
            key = (entry["question"].strip(), tuple(opt.strip() for opt in entry["options"]))
            if key in seen:
                duplicates.append({"entry": idx, "duplicate_with_entry": seen[key], "message": "Duplicate entry."})
            else:
                seen[key] = idx

        if duplicates:
            self.display_duplicates_pretty(duplicates)
            if self.purge_error_entries:
                self.remove_problematic_entries(duplicates)
        return len(duplicates)

    def display_duplicates_pretty(self, duplicates):
        console = Console()

        for duplicate in duplicates:
            original_idx = duplicate["duplicate_with_entry"]
            duplicate_idx = duplicate["entry"]
            original_entry = self.json_data[original_idx]
            duplicate_entry = self.json_data[duplicate_idx]

            tree = Tree(f"[bold blue]Duplicate Entry Found[/bold blue]")

            original_node = tree.add(f"Original Entry (Index: {original_idx})")
            duplicate_node = tree.add(f"Duplicate Entry (Index: {duplicate_idx})")

            for node, entry in [(original_node, original_entry), (duplicate_node, duplicate_entry)]:
                question_node = node.add("Question")
                question_node.add(Syntax(entry['question'], "text", theme="monokai", word_wrap=True))

                options_node = node.add("Options")
                for i, option in enumerate(entry['options'], 1):
                    options_node.add(f"{i}. {option}")

            console.print(Panel(tree, expand=False, border_style="blue"))
            console.print()

    def remove_problematic_entries(self, errors):
        self.json_data = [entry for idx, entry in enumerate(self.json_data) if idx not in {error['entry'] for error in errors}]

    def save_cleaned_data(self):
        base_filename = os.path.basename(self.json_file).split('.')[0]
        timestamp = datetime.now().strftime("%Y%m%d_%H%M%S")
        self.output_file = f"cleaned_{base_filename}_{timestamp}.json"
        with open(self.output_file, 'w', encoding='utf-8') as outfile:
            json.dump(self.json_data, outfile, ensure_ascii=False, indent=4)
        self.console.print(Panel(f"Step Three: Cleaned data saved to [green]{self.output_file}[/green]", style="bold green"))

    def run_all_checks(self):
        if not self.load_json_file():
            return
        self.clean_whitespace()

        is_valid = self.validate_all()

        if not is_valid:
            if self.purge_error_entries:
                self.console.print(Rule(title="JSON Evaluation Steps"))
                self.console.print(Panel("Step One: Entries with Errors will be purged.", style="bold magenta"))
                self.save_cleaned_data()
                self.revalidate_cleaned_data()
            else:
                self.console.print("[bold red]Issues found. They will NOT be automatically removed.[/bold red]")
        else:
            self.console.print(Panel("No issues found. JSON data is valid.", style="bold green"))

    def revalidate_cleaned_data(self):
        self.console.print(Panel("Step Four: Re-validating cleaned JSON data...", style="bold cyan"))
        is_valid = self.validate_all()

        if not is_valid:
            self.console.print(Panel("Re-validation failed. Errors found in the cleaned data.", style="bold red"))
        else:
            self.console.print(Panel("The re-validation of cleaned data passed successfully. New JSON should be error-free", style="bold green"))

    def clean_whitespace(self):
        for entry in self.json_data:
            entry.update({k: v.strip() if isinstance(v, str) else [i.strip() if isinstance(i, str) else i for i in v] if isinstance(v, list) else v for k, v in entry.items()})

# Set these variables as needed for your specific case
json_file = "/content/cleaned_merged_questions_with_answers.json"
purge_error_entries = True

evaluator = JSONEvaluator(json_file=json_file, purge_error_entries=purge_error_entries)
evaluator.run_all_checks()


Loading JSON file: /content/cleaned_merged_questions_with_answers.json

╭─────────────────────────────────────────────────────────────────────────────────────────────────────────────────╮
│ No issues found. JSON data is valid.                                                                            │
╰─────────────────────────────────────────────────────────────────────────────────────────────────────────────────╯

In [ ]:
# Convert 'answer' to string
merged_df['answer'] = merged_df['answer'].astype(str)


In [ ]:
import ast

# Convert 'options' from string to list if needed
merged_df['options'] = merged_df['options'].apply(lambda x: ast.literal_eval(x) if isinstance(x, str) else x)


In [ ]:
# Drop rows with missing 'original_question_num'
merged_df = merged_df.dropna(subset=['original_question_num'])

# Convert 'original_question_num' to integer
merged_df['original_question_num'] = merged_df['original_question_num'].astype(int)


In [ ]:
# Remove rows with empty 'answer' or 'options'
merged_df = merged_df.dropna(subset=['answer', 'options'])

# Remove rows where 'options' is not a list
merged_df = merged_df[merged_df['options'].apply(lambda x: isinstance(x, list))]


In [ ]:
# Convert the cleaned DataFrame to JSON
merged_json_path = '/content/cleaned_merged_results_with_answers.json'
merged_df.to_json(merged_json_path, orient='records', indent=4, force_ascii=False)

# Display the path to the JSON file
print(f"Converted cleaned DataFrame to JSON: {merged_json_path}")


Converted cleaned DataFrame to JSON: /content/cleaned_merged_results_with_answers.json


In [ ]:
# Set these variables as needed for your specific case
json_file = "/content/cleaned_merged_results_with_answers.json"  # Replace with the path to your JSON file
purge_error_entries = True  # Set to True if you want to purge error entries

evaluator = JSONEvaluator(json_file=json_file, purge_error_entries=purge_error_entries)
evaluator.run_all_checks()

Loading JSON file: /content/cleaned_merged_results_with_answers.json

╭────────────────────────────────────────────────────────────────────────╮
│ Error in Entry 15                                                      │
│ ├── Invalid 'answer': Answer cannot be more than number of options: 0. │
│ ├── Question                                                           │
│ │   └── ಜೀನು ಮತ್ತು ಕ್ರೋಮೋಸೋಮ್ ತಂತ್ರಜ್ಞಾನದಲ್ಲಿ ಅವರ ಉಪಯುಕ್ತತೆಯನ್ನು ಹೊಂದಿ:                       │
│ ├── Options                                                            │
│ └── Answer                                                             │
│     └── 4                                                              │
╰────────────────────────────────────────────────────────────────────────╯

╭────────────────────────────────────────────────────────────────────────╮
│ Error in Entry 50                                                      │
│ ├── Invalid 'answer': Answer cannot be more than number of options: 0. │
│ ├── Question                                                           │
│ │   └── ಈ ಕೆಳಗಿನವಗಳಲ್ಲಿ ಯಾವುದು?                                               │
│ ├── Options                                                            │
│ └── Answer                                                             │
│     └── 3                                                              │
╰────────────────────────────────────────────────────────────────────────╯

╭────────────────────────────────────────────────────────────────────────╮
│ Error in Entry 51                                                      │
│ ├── Invalid 'answer': Answer cannot be more than number of options: 0. │
│ ├── Question                                                           │
│ │   └── ವಾಯುಗಳಲ್ಲಿ ಸಂಯೋಜಕ ಶಕ್ತಿಯನ್ನು ಗುರುತಿಸಿ ಒದಗಿಸಿ :                                 │
│ ├── Options                                                            │
│ └── Answer                                                             │
│     └── 2                                                              │
╰────────────────────────────────────────────────────────────────────────╯

╭────────────────────────────────────────────────────────────────────────╮
│ Error in Entry 54                                                      │
│ ├── Invalid 'answer': Answer cannot be more than number of options: 0. │
│ ├── Question                                                           │
│ │   └── ಕೆಳಗಿನವುಗಳಲ್ಲಿ ಹೋಮೋಲಿಸ ಮತ್ತು ಸಂಯೋಜಕ ಶಕ್ತಿಯನ್ನು ಗುರುತಿಸಿ.                           │
│ ├── Options                                                            │
│ └── Answer                                                             │
│     └── 3                                                              │
╰────────────────────────────────────────────────────────────────────────╯

...

╭────────────────────────────────────────────────────────────────────────╮
│ Error in Entry 132                                                     │
│ ├── Invalid 'answer': Answer cannot be more than number of options: 0. │
│ ├── Question                                                           │
│ │   └── ಆಪ್ತಕೃತ ಮೌಲ್ಯಮಾಪನ ಹಾಗೂ ಸಸ್ಯಗಳಲ್ಲಿ ಆಪ್ತಕೃತ ಕೃತಕಾಂಗಗಳ ಸಂಯೋಜಿತಮಾಪನವು ಈ ಕೆಳಗಿನಗಳನ್ನು ಹೊಂದಿದೆ : │
│ ├── Options                                                            │
│ └── Answer                                                             │
│     └── 1                                                              │
╰────────────────────────────────────────────────────────────────────────╯

╭────────────────────────────────────────────────────────────────────────╮
│ Error in Entry 136                                                     │
│ ├── Invalid 'answer': Answer cannot be more than number of options: 0. │
│ ├── Question                                                           │
│ │   └── ಹುಳಗಣದ ಪರಂಪರಾ ಪ್ರಜಾತಿಗಳಲ್ಲಿ ತ್ರೈಲೋಕ್ಯ ಸುಂದರ ಮತ್ತು ಪ್ರಜಾಪತಿ ಸುಂದರ ಪ್ರಜಾತಿ ಉದಾಹರಣೆಯನ್ನು ಕೊಡಿ.  │
│ ├── Options                                                            │
│ └── Answer                                                             │
│     └── 3                                                              │
╰────────────────────────────────────────────────────────────────────────╯

╭────────────────────────────────────────────────────────────────────────╮
│ Error in Entry 138                                                     │
│ ├── Invalid 'answer': Answer cannot be more than number of options: 0. │
│ ├── Question                                                           │
│ │   └── ಆಕ್ಸಿನ್ ಪ್ರಕ್ರಿಯೆಯ ಸಂಯೋಜಕ ತತ್ವಗಳನ್ನು ಗುರುತಿಸಿ.                                 │
│ ├── Options                                                            │
│ └── Answer                                                             │
│     └── 3                                                              │
╰────────────────────────────────────────────────────────────────────────╯

╭────────────────────────────────────────────────────────────────────────╮
│ Error in Entry 142                                                     │
│ ├── Invalid 'answer': Answer cannot be more than number of options: 0. │
│ ├── Question                                                           │
│ │   └── ಕೆಳಗಿನ ಯಾವುದು ಸಂಯೋಜಕ ತತ್ವಗಳ ಪೈಕಿ ಯಾವ ತತ್ವಗಳಿಗೆ ಸೇರಿದೆ?                          │
│ ├── Options                                                            │
│ └── Answer                                                             │
│     └── 2                                                              │
╰────────────────────────────────────────────────────────────────────────╯

NameError: name 'Rule' is not defined

In [ ]:
import pandas as pd
import ast

# Assuming merged_df is your DataFrame

# 1. Convert 'answer' to string
merged_df['answer'] = merged_df['answer'].astype(str)

# 2. Convert 'options' from string to list if needed
merged_df['options'] = merged_df['options'].apply(lambda x: ast.literal_eval(x) if isinstance(x, str) else x)

# 3. Drop entries where 'answer' is out of range
def is_valid_row(row):
    if not isinstance(row['options'], list) or not row['options']:
        return False  # No valid options available
    try:
        answer_index = int(row['answer']) - 1
        return 0 <= answer_index < len(row['options'])
    except ValueError:
        return False  # Answer is not a valid number

# Drop rows with invalid answers or options
merged_df = merged_df[merged_df.apply(is_valid_row, axis=1)]

# 4. Drop entries with identical options
merged_df = merged_df[merged_df['options'].apply(lambda x: len(set(x)) > 1)]

# 5. Drop rows where 'original_question_num' is missing or empty
merged_df = merged_df.dropna(subset=['original_question_num'])

# 6. Convert the cleaned DataFrame to JSON
cleaned_json_path = '/content/cleaned_merged_results_with_answers1.json'
merged_df.to_json(cleaned_json_path, orient='records', indent=4, force_ascii=False)

print(f"Cleaned data saved to: {cleaned_json_path}")


Cleaned data saved to: /content/cleaned_merged_results_with_answers1.json


In [ ]:

json_file = "/content/cleaned_merged_questions_with_answers.json"
purge_error_entries = True

evaluator = JSONEvaluator(json_file=json_file, purge_error_entries=purge_error_entries)
evaluator.run_all_checks()

Loading JSON file: /content/cleaned_merged_questions_with_answers.json

╭─────────────────────────────────────────────────────────────────────────────────────────────────────────────────╮
│ No issues found. JSON data is valid.                                                                            │
╰─────────────────────────────────────────────────────────────────────────────────────────────────────────────────╯